In [ ]:
from utils.db import dbconn
conn = dbconn('dawndb')
import pandas as pd
pd.options.display.float_format = "{:,.2f}".format
df_rates = pd.read_sql_query("SELECT date, rate FROM rates where name='FED_FUND'",
                             conn,
                             parse_dates=['date'],
                             index_col=['date']).sort_index()
df_balances = pd.read_sql_query("SELECT * FROM strategy_im",
                                conn,
                                parse_dates=['date'],
                                index_col=['date']).sort_index()
df_balances[['broker', 'strategy']] = df_balances[['broker', 'strategy']].astype('category')

In [ ]:
from IPython.display import display
from pandas.tseries.offsets import BDay

def f(df_balances, df_rates, broker, start_date, end_date):
    df = (df_balances[df_balances.broker == broker].
      set_index("strategy", append=True)["amount"].
      unstack("strategy"))
    df[df.isnull()] = 0.
    drange = pd.date_range(pd.Timestamp(start_date) - BDay(), end_date)
    rates = df_rates.reindex(drange, method="ffill").values /100 /360
    df = df.reindex(drange, method="ffill") * rates
    df = df.loc[start_date:]
    display(df.sum().to_frame(name='amount'))
    print(df.sum().sum())
    
from functools import partial
f_print = partial(f, df_balances, df_rates)

In [ ]:
from ipywidgets import widgets, Layout
import datetime
broker_widget = widgets.Dropdown(
    options=df_balances.broker.cat.categories,
    value='CITI',
    description='Broker:',
    disabled=False,
)
start_date = widgets.DatePicker(
    description='start:',
    disabled=False,
    value=datetime.date(2019, 6, 1)
)
end_date = widgets.DatePicker(
    description='end:',
    disabled=False,
    value=datetime.date(2019, 6, 30)
)
output = widgets.interactive_output(f_print, {'broker': broker_widget, 'start_date': start_date, 'end_date': end_date})
output.layout= Layout(margin='auto auto auto 90px')
widgets.VBox([widgets.HBox([broker_widget, start_date, end_date]), output])

In [ ]:
f(df_balances, df_rates, "MS", "2019-06-01", "2019-06-30").sum(axis=1)

In [ ]:
df_balances[df_balances.broker=='MS'].loc["2019-06-10"]